# پروڈکشن میں آٹو جن ایجنٹس: مشاہدہ اور جانچ

اس سبق میں، ہم سیکھیں گے کہ **[آٹو جن ایجنٹس](https://github.com/microsoft/autogen)** کے اندرونی مراحل (ٹریسز) کی نگرانی کیسے کریں** اور [لانگ فیوز](https://langfuse.com) کا استعمال کرتے ہوئے اس کی کارکردگی کا جائزہ کیسے لیں۔ 

یہ گائیڈ ان ٹیموں کے لیے **آن لائن** اور **آف لائن** جانچ کے پیمانے کا احاطہ کرتا ہے جو ایجنٹس کو تیزی اور اعتماد کے ساتھ پروڈکشن میں لانا چاہتی ہیں۔

**کیوں AI ایجنٹ کی جانچ ضروری ہے:**
- جب کام ناکام ہوں یا غیر معیاری نتائج دیں تو مسائل کو ڈیبگ کرنا
- حقیقی وقت میں لاگت اور کارکردگی کی نگرانی کرنا
- مسلسل فیڈبیک کے ذریعے اعتماد اور حفاظت کو بہتر بنانا


## مرحلہ 1: ماحول کے متغیرات سیٹ کریں

[Langfuse Cloud](https://cloud.langfuse.com/) پر سائن اپ کرکے یا [Langfuse کو خود ہوسٹ کرکے](https://langfuse.com/self-hosting) اپنے Langfuse API کیز حاصل کریں۔

_**نوٹ:** خود ہوسٹ کرنے والے [Terraform ماڈیولز](https://langfuse.com/self-hosting/azure) کا استعمال کرکے Azure پر Langfuse کو ڈپلائے کر سکتے ہیں۔ متبادل کے طور پر، آپ [Helm چارٹ](https://langfuse.com/self-hosting/kubernetes-helm) کا استعمال کرتے ہوئے Kubernetes پر Langfuse کو ڈپلائے کر سکتے ہیں۔_


In [5]:
import os

# Get keys for your project from the project settings page: https://cloud.langfuse.com
os.environ["LANGFUSE_PUBLIC_KEY"] = "pk-lf-..." 
os.environ["LANGFUSE_SECRET_KEY"] = "sk-lf-..." 
os.environ["LANGFUSE_HOST"] = "https://cloud.langfuse.com" # 🇪🇺 EU region
# os.environ["LANGFUSE_HOST"] = "https://us.cloud.langfuse.com" # 🇺🇸 US region

ماحولیاتی متغیرات کے سیٹ ہونے کے بعد، ہم اب لینگ فیوز کلائنٹ کو ابتدائی شکل دے سکتے ہیں۔ `get_client()` ماحولیاتی متغیرات میں فراہم کردہ اسناد کا استعمال کرتے ہوئے لینگ فیوز کلائنٹ کو ابتدائی شکل دیتا ہے۔


In [6]:
from langfuse import Langfuse
 
# Filter out Autogen OpenTelemetryspans
langfuse = Langfuse(
    blocked_instrumentation_scopes=["autogen SingleThreadedAgentRuntime"]
)
 
# Verify connection
if langfuse.auth_check():
    print("Langfuse client is authenticated and ready!")
else:
    print("Authentication failed. Please check your credentials and host.")

Langfuse client is authenticated and ready!


## مرحلہ 2: اوپن لِٹ انسٹرومنٹیشن کو شروع کریں

اب ہم [اوپن لِٹ](https://github.com/openlit/openlit) انسٹرومنٹیشن کو شروع کرتے ہیں۔ اوپن لِٹ خودکار طور پر آٹو جین آپریشنز کو کیپچر کرتا ہے اور اوپن ٹیلیمیٹری (OTel) اسپینز کو لینگ فیوز میں ایکسپورٹ کرتا ہے۔


In [7]:
import openlit
 
# Initialize OpenLIT instrumentation. The disable_batch flag is set to true to process traces immediately.
openlit.init(tracer=langfuse._otel_tracer, disable_batch=True, disabled_instrumentors=["mistral"])

## مرحلہ 3: اپنے ایجنٹ کو چلائیں

اب ہم اپنے آلات کی جانچ کے لیے ایک کثیر مرحلہ ایجنٹ ترتیب دیتے ہیں۔


In [2]:
import os

from autogen_agentchat.agents import AssistantAgent
from autogen_ext.models.azure import AzureAIChatCompletionClient
from azure.core.credentials import AzureKeyCredential
from autogen_agentchat.base import TaskResult

from autogen_agentchat.conditions import TextMentionTermination
from autogen_agentchat.teams import RoundRobinGroupChat

In [3]:
client = AzureAIChatCompletionClient(
    model="gpt-4o-mini",
    endpoint="https://models.inference.ai.azure.com",
    # To authenticate with the model you will need to generate a personal access token (PAT) in your GitHub settings.
    # Create your PAT token by following instructions here: https://docs.github.com/en/authentication/keeping-your-account-and-data-secure/managing-your-personal-access-tokens
    credential=AzureKeyCredential(os.environ["GITHUB_TOKEN"]),
    model_info={
        "json_output": True,
        "function_calling": True,
        "vision": True,
        "family": "unknown",
        "structured_output": False
    },
)

In [8]:
# 🍴 Agent 1 – proposes ONE healthy meal idea each turn
meal_planner_agent = AssistantAgent(
    "meal_planner_agent",
    model_client=client,
    description="A seasoned meal-planning coach who suggests balanced meals.",
    system_message="""
    You are a Meal-Planning Assistant with a decade of experience helping busy people prepare meals.
    Goal: propose the single best meal (breakfast, lunch, or dinner) given the user's context.
    Each response must contain ONLY one complete meal idea (title + very brief component list) — no extras.
    Keep it concise: skip greetings, chit-chat, and filler.
    """,
)

# 🥗 Agent 2 – checks nutritional quality & variety
nutritionist_agent = AssistantAgent(
    "nutritionist_agent",
    model_client=client,
    description="A registered dietitian ensuring meals meet nutritional standards.",
    system_message="""
    You are a Nutritionist focused on whole-food, macro-balanced eating.
    Evaluate the meal_planner_agent’s recommendation.
    If the meal is nutritionally sound, sufficiently varied, and portion-appropriate, respond with 'APPROVE'.
    Otherwise, give high-level guidance on how to improve it (e.g. 'add a plant-based protein') — do NOT provide a full alternative recipe.
    """,
)

In [9]:
# ✅ Chat stops once the nutritionist says APPROVE
termination = TextMentionTermination("APPROVE")

# 🔄 Alternate turns between the two agents until termination
team = RoundRobinGroupChat(
    [meal_planner_agent, nutritionist_agent],
    termination_condition=termination,
)

# Example kickoff
user_input = "I'm looking for a quick, delicious dinner I can prep after work. I have 30 minutes and minimal clean-up is ideal."

In [ ]:
with langfuse.start_as_current_span(name="create_meal_plan") as span:
    async for message in team.run_stream(task=user_input):
        if isinstance(message, TaskResult):
            print("Stop Reason:", message.stop_reason)
        else:
            print(message)

    span.update_trace(
        input=user_input,
        output=message.stop_reason,
    )

# Flush the trace to Langfuse for short-lived environments such as Jupyter Notebooks
langfuse.flush()

### ٹریس کی ساخت

Langfuse ایک **ٹریس** ریکارڈ کرتا ہے جس میں **اسپینز** شامل ہوتے ہیں، جو آپ کے ایجنٹ کی منطق کے ہر مرحلے کی نمائندگی کرتے ہیں۔ یہاں، ٹریس میں مجموعی ایجنٹ کے عمل اور ذیلی اسپینز شامل ہیں:
- کھانے کی منصوبہ بندی کرنے والا ایجنٹ
- غذائیت کے ماہرین کے ایجنٹس

آپ ان کا معائنہ کر سکتے ہیں تاکہ یہ دیکھ سکیں کہ وقت کہاں صرف ہوا، کتنے ٹوکن استعمال ہوئے، اور دیگر تفصیلات:

![Langfuse میں ٹریس کا درخت](https://langfuse.com/images/cookbook/example-autogen-evaluation/trace-tree.png)

_[ٹریس کا لنک](https://cloud.langfuse.com/project/cloramnkj0002jz088vzn1ja4/traces/dac2b33e7cd709e685ccf86a137ecc64)_


## آن لائن جائزہ

آن لائن جائزہ سے مراد ایجنٹ کا جائزہ لینا ایک حقیقی، عملی ماحول میں ہے، یعنی پروڈکشن کے دوران اصل استعمال کے وقت۔ اس میں ایجنٹ کی کارکردگی کو حقیقی صارف کے تعاملات پر نظر رکھنا اور نتائج کا مسلسل تجزیہ شامل ہے۔

### پروڈکشن میں ٹریک کرنے کے عام میٹرکس

1. **اخراجات** — انسٹرومنٹیشن ٹوکن کے استعمال کو ریکارڈ کرتی ہے، جسے آپ ہر ٹوکن کی قیمت مقرر کرکے تقریباً اخراجات میں تبدیل کر سکتے ہیں۔
2. **تاخیر** — ہر مرحلے یا پورے عمل کو مکمل کرنے میں لگنے والے وقت کا مشاہدہ کریں۔
3. **صارف کی رائے** — صارفین براہ راست رائے (مثلاً، thumbs up/down) دے سکتے ہیں تاکہ ایجنٹ کو بہتر یا درست کیا جا سکے۔
4. **LLM-as-a-Judge** — ایک الگ LLM استعمال کریں تاکہ آپ کے ایجنٹ کے نتائج کا تقریباً حقیقی وقت میں جائزہ لیا جا سکے (مثلاً، زہریلے مواد یا درستگی کی جانچ کرنا)۔

نیچے، ہم ان میٹرکس کی مثالیں دکھاتے ہیں۔


#### 1. اخراجات

نیچے ایک اسکرین شاٹ دکھایا گیا ہے جو `gpt-4o-mini` کالز کے استعمال کو ظاہر کرتا ہے۔ یہ مہنگے مراحل کو دیکھنے اور اپنے ایجنٹ کو بہتر بنانے کے لیے مفید ہے۔

![اخراجات](https://langfuse.com/images/cookbook/example-autogen-evaluation/gpt-4o-costs.png)

_[ٹریس کے لیے لنک](https://cloud.langfuse.com/project/cloramnkj0002jz088vzn1ja4/traces/dac2b33e7cd709e685ccf86a137ecc64)_


#### 2. تاخیر

ہم یہ بھی دیکھ سکتے ہیں کہ ہر مرحلہ مکمل کرنے میں کتنا وقت لگا۔ نیچے دیے گئے مثال میں، پورے عمل میں تقریباً 3 سیکنڈ لگے، جسے آپ مرحلہ وار تقسیم کر سکتے ہیں۔ یہ آپ کو رکاوٹوں کی نشاندہی کرنے اور اپنے ایجنٹ کو بہتر بنانے میں مدد دیتا ہے۔

![تاخیر](https://langfuse.com/images/cookbook/example-autogen-evaluation/agent-latency.png)

_[ٹریس کے لیے لنک](https://cloud.langfuse.com/project/cloramnkj0002jz088vzn1ja4/traces/dac2b33e7cd709e685ccf86a137ecc64?display=timeline)_


#### 3. صارف کی رائے

اگر آپ کا ایجنٹ کسی یوزر انٹرفیس میں شامل ہے، تو آپ براہ راست صارف کی رائے ریکارڈ کر سکتے ہیں (جیسے چیٹ انٹرفیس میں انگوٹھا اوپر/نیچے کا آپشن)۔


In [10]:
from langfuse import get_client
 
langfuse = get_client()
 
# Option 1: Use the yielded span object from the context manager
with langfuse.start_as_current_span(
    name="autogen-request-user-feedback-1") as span:
    
    async for message in team.run_stream(task="Create a meal with potatoes"):
            if isinstance(message, TaskResult):
                print("Stop Reason:", message.stop_reason)
            else:
                print(message)    
 
    # Score using the span object
    span.score_trace(
        name="user-feedback",
        value=1,
        data_type="NUMERIC",
        comment="This was delicious, thank you"
    )
 
# Option 2: Use langfuse.score_current_trace() if still in context
with langfuse.start_as_current_span(name="autogen-request-user-feedback-2") as span:
    # ... Autogen execution ...

    async for message in team.run_stream(task="I am allergic to gluten."):
            if isinstance(message, TaskResult):
                print("Stop Reason:", message.stop_reason)
            else:
                print(message)    
 
    # Score using current context
    langfuse.score_current_trace(
        name="user-feedback",
        value=1,
        data_type="NUMERIC"
    )

id='da068880-22ae-4f01-9f01-2bb231939089' source='user' models_usage=None metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 20, 43, 732669, tzinfo=datetime.timezone.utc) content='Create a meal with potatoes' type='TextMessage'
id='ad937ce4-3534-493f-824b-ca9c226b5287' source='meal_planner_agent' models_usage=RequestUsage(prompt_tokens=95, completion_tokens=30) metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 20, 45, 186423, tzinfo=datetime.timezone.utc) content='Potato and Spinach Frittata  \n- Eggs  \n- Potatoes  \n- Fresh spinach  \n- Onion  \n- Cheese (optional)  ' type='TextMessage'
id='50fd33c1-057f-49fe-afad-ee86d164296d' source='nutritionist_agent' models_usage=RequestUsage(prompt_tokens=132, completion_tokens=4) metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 20, 45, 581059, tzinfo=datetime.timezone.utc) content='APPROVE' type='TextMessage'
Stop Reason: Text 'APPROVE' mentioned
id='e371de6c-e5fc-42c1-8eda-e5b8cd5accab' source='user' models_usage=None met

In [ ]:
# Option 3: Use create_score() with trace ID (when outside context)
langfuse.create_score(
    trace_id="predefined_trace_id",
    name="user-feedback",
    value=1,
    data_type="NUMERIC",
    comment="This was correct, thank you"
)

صارف کی رائے پھر لینگ فیوز میں محفوظ کی جاتی ہے:

![صارف کی رائے لینگ فیوز میں محفوظ کی جا رہی ہے](https://langfuse.com/images/cookbook/example-autogen-evaluation/user-feedback.png)


#### 4. خودکار LLM-as-a-Judge اسکورنگ

LLM-as-a-Judge آپ کے ایجنٹ کے نتائج کو خودکار طور پر جانچنے کا ایک اور طریقہ ہے۔ آپ ایک الگ LLM کال ترتیب دے سکتے ہیں تاکہ نتائج کی درستگی، زہریلا پن، انداز، یا کسی اور معیار کو جانچا جا سکے جو آپ کے لیے اہم ہو۔

**ورک فلو**:
1. آپ ایک **ایویلیوایشن ٹیمپلیٹ** تعریف کرتے ہیں، جیسے "چیک کریں کہ آیا متن زہریلا ہے۔"
2. آپ ایک ماڈل سیٹ کرتے ہیں جو جج-ماڈل کے طور پر استعمال ہوتا ہے؛ اس کیس میں `gpt-4o-mini` جو Azure کے ذریعے کوئری کیا جاتا ہے۔
3. جب بھی آپ کا ایجنٹ نتائج پیدا کرتا ہے، آپ وہ نتائج اپنے "جج" LLM کو ٹیمپلیٹ کے ساتھ بھیجتے ہیں۔
4. جج LLM ایک ریٹنگ یا لیبل کے ساتھ جواب دیتا ہے جسے آپ اپنے مشاہداتی ٹول میں لاگ کرتے ہیں۔

Langfuse سے مثال:

![LLM-as-a-Judge Evaluator](https://langfuse.com/images/cookbook/example-autogen-evaluation/evaluator.png)


In [12]:
with langfuse.start_as_current_span(name="autogen-request-user-feedback-2") as span:

    async for message in team.run_stream(task="I am a picky eater and not sure if you find something for me."):
            if isinstance(message, TaskResult):
                print("Stop Reason:", message.stop_reason)
            else:
                print(message) 

    span.update_trace(
        input=user_input,
        output=message.stop_reason,
    )

langfuse.flush()

id='eefc628d-502f-451a-8f70-be486f62f8c5' source='user' models_usage=None metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 38, 29, 171393, tzinfo=datetime.timezone.utc) content='I am a picky eater and not sure if you find something for me.' type='TextMessage'
id='13b3e14b-bcf7-42a5-80d6-54b0c7be765e' source='meal_planner_agent' models_usage=RequestUsage(prompt_tokens=352, completion_tokens=27) metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 38, 30, 433516, tzinfo=datetime.timezone.utc) content='Chicken Alfredo Pasta  \n- Gluten-free pasta  \n- Grilled chicken breast  \n- Heavy cream  \n- Parmesan cheese  \n- Garlic  ' type='TextMessage'
id='550f2dee-0e08-4bbd-b67f-991b467328f1' source='nutritionist_agent' models_usage=RequestUsage(prompt_tokens=386, completion_tokens=17) metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 38, 31, 505173, tzinfo=datetime.timezone.utc) content='Consider incorporating some vegetables, like spinach or broccoli, to increase the nutrien

آپ دیکھ سکتے ہیں کہ اس مثال کے جواب کو "غیر زہریلا" قرار دیا گیا ہے۔

![LLM-as-a-Judge Evaluation Score](https://langfuse.com/images/cookbook/example-autogen-evaluation/llm-as-a-judge-score.png)


#### 5. مشاہداتی میٹرکس کا جائزہ

یہ تمام میٹرکس ڈیش بورڈز میں ایک ساتھ دیکھے جا سکتے ہیں۔ اس سے آپ کو یہ جلدی سمجھنے میں مدد ملتی ہے کہ آپ کا ایجنٹ مختلف سیشنز میں کیسا کام کر رہا ہے اور وقت کے ساتھ معیار کے میٹرکس کو ٹریک کرنے میں آسانی ہوتی ہے۔

![مشاہداتی میٹرکس کا جائزہ](https://langfuse.com/images/cookbook/example-autogen-evaluation/dashboard.png)


## آف لائن جائزہ

آن لائن جائزہ براہ راست فیڈبیک کے لیے ضروری ہے، لیکن آپ کو **آف لائن جائزہ** کی بھی ضرورت ہوتی ہے—ترقی سے پہلے یا دوران منظم جانچ۔ یہ پیداوار میں تبدیلیاں شامل کرنے سے پہلے معیار اور اعتماد کو برقرار رکھنے میں مدد دیتا ہے۔


### ڈیٹاسیٹ کا جائزہ

آف لائن جائزے میں، آپ عام طور پر یہ کرتے ہیں:
1. ایک معیار ڈیٹاسیٹ رکھتے ہیں (جس میں پرامپٹ اور متوقع نتائج کے جوڑے شامل ہوں)
2. اپنے ایجنٹ کو اس ڈیٹاسیٹ پر چلاتے ہیں
3. نتائج کا موازنہ متوقع نتائج سے کرتے ہیں یا کسی اضافی اسکورنگ میکانزم کا استعمال کرتے ہیں

نیچے، ہم اس طریقہ کار کو [q&a-dataset](https://huggingface.co/datasets/junzhang1207/search-dataset) کے ساتھ ظاہر کرتے ہیں، جس میں سوالات اور متوقع جوابات شامل ہیں۔


In [16]:
import pandas as pd
from datasets import load_dataset
 
# Fetch search-dataset from Hugging Face
dataset = load_dataset("junzhang1207/search-dataset", split = "train")
df = pd.DataFrame(dataset)
print("First few rows of search-dataset:")
print(df.head())

/Users/jannik/Documents/GitHub/ai-agents-for-beginners/.venv/lib/python3.13/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


First few rows of search-dataset:
                                     id  \
0  20caf138-0c81-4ef9-be60-fe919e0d68d4   
1  1f37d9fd-1bcc-4f79-b004-bc0e1e944033   
2  76173a7f-d645-4e3e-8e0d-cca139e00ebe   
3  5f5ef4ca-91fe-4610-a8a9-e15b12e3c803   
4  64dbed0d-d91b-4acd-9a9c-0a7aa83115ec   

                                            question  \
0                 steve jobs statue location budapst   
1  Why is the Battle of Stalingrad considered a t...   
2  In what year did 'The Birth of a Nation' surpa...   
3  How many Russian soldiers surrendered to AFU i...   
4   What event led to the creation of Google Images?   

                                     expected_answer       category       area  
0  The Steve Jobs statue is located in Budapest, ...           Arts  Knowledge  
1  The Battle of Stalingrad is considered a turni...   General News       News  
2  This question is based on a false premise. 'Th...  Entertainment       News  
3  About 300 Russian soldiers surrendered to t

اگلا، ہم Langfuse میں ایک ڈیٹاسیٹ entity بناتے ہیں تاکہ رنز کو ٹریک کیا جا سکے۔ پھر، ہم ڈیٹاسیٹ سے ہر آئٹم کو سسٹم میں شامل کرتے ہیں۔


In [17]:
from langfuse import Langfuse
langfuse = Langfuse()
 
langfuse_dataset_name = "qa-dataset_autogen-agent"
 
# Create a dataset in Langfuse
langfuse.create_dataset(
    name=langfuse_dataset_name,
    description="q&a dataset uploaded from Hugging Face",
    metadata={
        "date": "2025-03-21",
        "type": "benchmark"
    }
)

Dataset(id='cmcm7524d00kjad07s2cjwqcf', name='qa-dataset_autogen-agent', description='q&a dataset uploaded from Hugging Face', metadata={'date': '2025-03-21', 'type': 'benchmark'}, project_id='cloramnkj0002jz088vzn1ja4', created_at=datetime.datetime(2025, 7, 2, 16, 54, 7, 357000, tzinfo=datetime.timezone.utc), updated_at=datetime.datetime(2025, 7, 2, 16, 54, 7, 357000, tzinfo=datetime.timezone.utc))

In [18]:
df_25 = df.sample(25) # For this example, we upload only 25 dataset questions

for idx, row in df_25.iterrows():
    langfuse.create_dataset_item(
        dataset_name=langfuse_dataset_name,
        input={"text": row["question"]},
        expected_output={"text": row["expected_answer"]}
    )

![ڈیٹاسیٹ آئٹمز لینگ فیوز میں](https://langfuse.com/images/cookbook/example-autogen-evaluation/example-dataset.png)


#### ڈیٹاسیٹ پر ایجنٹ چلانا

سب سے پہلے، ہم ایک سادہ Autogen ایجنٹ تیار کرتے ہیں جو Azure OpenAI ماڈلز کا استعمال کرتے ہوئے سوالات کے جوابات دیتا ہے۔


In [8]:
import os
from dotenv import load_dotenv

from autogen_agentchat.agents import AssistantAgent
from autogen_core.models import UserMessage
from autogen_ext.models.azure import AzureAIChatCompletionClient
from azure.core.credentials import AzureKeyCredential
from autogen_core import CancellationToken
from autogen_agentchat.messages import TextMessage

In [ ]:
load_dotenv()
client = AzureAIChatCompletionClient(
    model="gpt-4o",
    endpoint="https://models.inference.ai.azure.com",
    # To authenticate with the model you will need to generate a personal access token (PAT) in your GitHub settings.
    # Create your PAT token by following instructions here: https://docs.github.com/en/authentication/keeping-your-account-and-data-secure/managing-your-personal-access-tokens
    credential=AzureKeyCredential(os.getenv("GITHUB_TOKEN")),
    max_tokens=5000,
    model_info={
        "json_output": True,
        "function_calling": False,
        "vision": False,
        "family": "unknown",
        "structured_output": True,
    },
)

result = await client.create([UserMessage(content="What is the capital of France?", source="user")])
print(result)

In [18]:
agent = AssistantAgent(
    name="assistant",
    model_client=client,
    tools=[],
    system_message="You are participant in a quizz show and you are given a question. You need to create a short answer to the question.",
)

پھر، ہم ایک مددگار فنکشن `my_agent()` کی تعریف کرتے ہیں۔


In [19]:
async def my_agent(user_query: str):

    with langfuse.start_as_current_span(name="autogen-trace") as span:

        # Execute the agent response
        response = await agent.on_messages(
            [TextMessage(content=user_query, source="user")],
            cancellation_token=CancellationToken(),
        )

        span.update_trace(
            input=user_query,
            output=response.chat_message.content,
        )

    return str(response.chat_message.content)

# Test the function
await my_agent("What is the capital of France?")

'The capital of France is Paris.'

آخر میں، ہم ہر ڈیٹاسیٹ آئٹم پر لوپ کرتے ہیں، ایجنٹ کو چلاتے ہیں، اور ٹریس کو ڈیٹاسیٹ آئٹم سے جوڑتے ہیں۔ اگر چاہیں تو ہم ایک فوری تشخیصی اسکور بھی شامل کر سکتے ہیں۔


In [20]:
dataset_name = "qa-dataset_autogen-agent"
current_run_name = "dev_tasks_run-autogen_gpt-4.1" # Identifies this specific evaluation run
current_run_metadata={"model_provider": "Azure", "model": "gpt-4.1"}
current_run_description="Evaluation run for Autogen model on July 3rd"

dataset = langfuse.get_dataset('qa-dataset_autogen-agent')

for item in dataset.items:
    print(f"Running evaluation for item: {item.id} (Input: {item.input})")
 
    # Use the item.run() context manager
    with item.run(
        run_name=current_run_name,
        run_metadata=current_run_metadata,
        run_description=current_run_description
    ) as root_span: 
        # All subsequent langfuse operations within this block are part of this trace.
        generated_answer = await my_agent(user_query = item.input["text"])
    
    print("Generated Answer: ", generated_answer)
 
print(f"\nFinished processing dataset '{dataset_name}' for run '{current_run_name}'.")

langfuse.flush()

Running evaluation for item: 09810cc4-9992-4712-a3b2-7224da31776a (Input: {'text': 'In Hindu mythology, which deity is the Ganges river dolphin associated with?'})
Generated Answer:  In Hindu mythology, the Ganges river dolphin is associated with the deity Ganga.
Running evaluation for item: bb113f94-7723-47c6-8c34-59d883044514 (Input: {'text': 'What significant discovery did the LHCb collaboration report in 2015?'})
Generated Answer:  In 2015, the LHCb collaboration reported the discovery of pentaquark particles.
Running evaluation for item: 4d8ae54e-ceab-46d0-ad2c-6e8e223589a9 (Input: {'text': 'What is the MÄ\x81ori name for the red-crowned parakeet?'})
Generated Answer:  The Māori name for the red-crowned parakeet is kākāriki.
Running evaluation for item: 21e5a0d5-f619-4a73-868e-9955053b3e72 (Input: {'text': 'Who starred in the 1978 television film adaptation of Les MisÃ©rables?'})
Generated Answer:  Richard Jordan starred as Jean Valjean in the 1978 television film adaptation of Le

اہم قواعد:
1. مختلف ایجنٹ کنفیگریشنز کے ساتھ اس عمل کو دہرایا جا سکتا ہے، جیسے:
   - ماڈلز (gpt-4o-mini، gpt-4.1، وغیرہ)
   - پرامپٹس
   - ٹولز (سرچ بمقابلہ بغیر سرچ)
   - ایجنٹ کی پیچیدگی (ملٹی ایجنٹ بمقابلہ سنگل ایجنٹ)

2. پھر ان کا موازنہ Langfuse میں ساتھ ساتھ کیا جا سکتا ہے۔ اس مثال میں، میں نے ایجنٹ کو 25 ڈیٹاسیٹ سوالات پر 3 بار چلایا۔ ہر بار، میں نے ایک مختلف Azure OpenAI ماڈل استعمال کیا۔ آپ دیکھ سکتے ہیں کہ بڑے ماڈل استعمال کرنے پر درست جوابات کی تعداد میں اضافہ ہوتا ہے (جیسا کہ توقع کی جاتی ہے)۔ `correct_answer` اسکور ایک [LLM-as-a-Judge Evaluator](https://langfuse.com/docs/scores/model-based-evals) کے ذریعے بنایا گیا ہے، جو ڈیٹاسیٹ میں دیے گئے نمونہ جواب کی بنیاد پر سوال کی درستگی کا فیصلہ کرنے کے لیے ترتیب دیا گیا ہے۔

![ڈیٹاسیٹ رن کا جائزہ](https://langfuse.com/images/cookbook/example-autogen-evaluation/dataset_runs.png)
![ڈیٹاسیٹ رن کا موازنہ](https://langfuse.com/images/cookbook/example-autogen-evaluation/dataset-run-comparison.png)



---

**ڈسکلیمر**:  
یہ دستاویز AI ترجمہ سروس [Co-op Translator](https://github.com/Azure/co-op-translator) کا استعمال کرتے ہوئے ترجمہ کی گئی ہے۔ ہم درستگی کے لیے کوشش کرتے ہیں، لیکن براہ کرم آگاہ رہیں کہ خودکار ترجمے میں غلطیاں یا عدم درستگی ہو سکتی ہیں۔ اصل دستاویز، جو اس کی مقامی زبان میں ہے، کو مستند ذریعہ سمجھا جانا چاہیے۔ اہم معلومات کے لیے، پیشہ ور انسانی ترجمہ کی سفارش کی جاتی ہے۔ اس ترجمے کے استعمال سے پیدا ہونے والی کسی بھی غلط فہمی یا غلط تشریح کے لیے ہم ذمہ دار نہیں ہیں۔
